In this notebook, we will look at the accidents data of Heidelberg.

In [1]:
import os
import folium
import matplotlib as plt
import matplotlib.colors as mcolors
import seaborn as sns
import polars as pl
from data_io.loader.data_loader import DataLoader
import analysis.visualization.accidents.acc_analytics as ana

In [19]:
dl = DataLoader()

# Heidelberg
acc = (
    dl.accident_data
    .bicycle_only()
    .filter_region(state=8, region=2, district=21)
)

points = acc.map_points()

Holidays folder not found: ./data/processed/holidays/


In [3]:
years = sorted(acc.df["year"].unique().to_list())
cmap = plt.colormaps['viridis']
year_colors = {
    year: mcolors.rgb2hex(cmap(i / (len(years)-1)))
    for i, year in enumerate(years)
}

Show the map of all accidents (2016-2024) which includes bicyle in a accident.

In [4]:
center = acc.df.select(["latitude", "longitude"]).mean().to_numpy()[0].tolist()

m = folium.Map(location=center, zoom_start=13)

for lat, lon, year, month in points:
    folium.CircleMarker(
        location=[lat, lon],
        radius=5,
        popup=f"Year: {year}, Month: {month}",
        color=year_colors[year],
        fill=True,
        fill_color=year_colors[year],
        fill_opacity=0.7
    ).add_to(m)

legend_html = '''
     <div style="
         position: fixed;
         bottom: 50px;
         left: 50px;
         width: 150px;
         height: auto;
         border: 2px solid grey;
         z-index: 9999;
         background-color: white;
         padding: 10px;
         font-size: 14px;
     ">
     <b>Accident Years</b><br>
'''

for year in years:
    color = year_colors[year]
    legend_html += f'''
        <i style="
            background:{color};
            width:12px;
            height:12px;
            float:left;
            margin-right:6px;
            opacity:0.9;
        "></i>{year}<br>
    '''

legend_html += "</div>"

m.get_root().html.add_child(folium.Element(legend_html))

m

Show all accidents in a specific radius in meter of each counter

In [8]:
RADIUS = 50

df_stats = ana.calculate_station_stats(dl, radius_meters=RADIUS)

print(f"Top 10 Stationen (Radius {RADIUS}m):")
print(df_stats.head(15))

Analysiere 15 Stationen gegen 2098019 Unfälle mit Radius 50m...
Top 10 Stationen (Radius 50m):
shape: (15, 4)
┌─────────────────────────────────┬──────────────┬───────────────┬────────────────┐
│ Station                         ┆ Alle Unfälle ┆ Davon Fahrrad ┆ Fahrrad-Anteil │
│ ---                             ┆ ---          ┆ ---           ┆ ---            │
│ str                             ┆ i64          ┆ i64           ┆ f64            │
╞═════════════════════════════════╪══════════════╪═══════════════╪════════════════╡
│ Thedor-Heuss-Brücke Querschnit… ┆ 13           ┆ 10            ┆ 0.769231       │
│ Plöck                           ┆ 9            ┆ 8             ┆ 0.888889       │
│ Gaisbergstraße                  ┆ 9            ┆ 7             ┆ 0.777778       │
│ Ernst-Walz-Brücke West - alt    ┆ 7            ┆ 5             ┆ 0.714286       │
│ Rohrbacher Straße Querschnitt   ┆ 5            ┆ 5             ┆ 1.0            │
│ …                               ┆ …            ┆

Show the map with all counters and the specific radius.
(TODO, individual radius for each Station?)

In [6]:
m = ana.plot_accident_validation_map(dl, radius_meters=RADIUS)
m